
## Extração da dimensão d_ncm para a camada gold


In [0]:
%sql

-- faz um select para verificar a tabela que está na camada bronze

select * from bronze.co_ncm

CO_NCM CO_UNID CO_SH6 CO_PPE CO_PPI CO_FAT_AGREG CO_CUCI_ITEM CO_CGCE_N3 CO_SIIT CO_ISIC_CLASSE CO_EXP_SUBSET NO_NCM_POR NO_NCM_ESP NO_NCM_ING 38085910 10 380859 3293 3293 3 5919 322 2000 2021 1499 Outras mercadorias mencionadas na Nota de subposições 1 do presente Capítulo, apresentadas em formas ou embalagens exclusivamente para uso direto em aplicações domissanitárias Otros productos mencionados en la nota de subpartida 1 deste Capítulo, presentados en formas o envases exclusivamente para su uso directo en aplicaciones sanitarias Other commodities mentioned in Note of subheading 1 of htis Chapter, presented in forms or packings exclusively for direct use in sanitary applications 38085921 10 380859 3293 3293 3 5919 240 2000 2021 1499 Mercadorias à base de metamidofós (ISO) ou monocrotofós (ISO), apresentadas de outro modo Productos basados en metamidofos (ISO) o monocrotofos (ISO), presentados de otro modo Commodities based on methamidophos (ISO) or monocrotophos (ISO), presented otherwise 38085922 10 380859 3293 3293 3 5919 240 2000 2021 1499 Mercadorias à base de endossulfan (ISO), apresentadas de outro modo Productos sobre la base de endosulfán (ISO), presentados de otro modo Commodities based on endosulfan (ISO), presented otherwise 38085923 10 380859 3293 3293 3 5919 322 2000 2021 1499 Mercadorias à base de alaclor (ISO), apresentadas de outro modo Productos sobre la base de alaclor (ISO), presentados de otro modo Commodities based on alachlor (ISO), presented otherwise 38085929 10 380859 3293 3293 3 5919 240 2000 2021 1499 Mercadorias à base de outras substâncias, apresentadas de outro modo Las mercancías sobre la base de otras sustancias, presentados de otro modo Commodities based on other substances, presented otherwise 38249914 10 382499 3990 3639 3 59899 240 2000 2029 1499 Senduramicina sódica, da fabricação da senduramicina Senduramicina de sodio, de la fabricación de senduramicina Sodium senduramicina, from the manufacturing process of senduramicina 38249915 10 382499 3990 3639 3 59899 240 2000 2029 1499 Maduramicina amônica, em solução alcoólica, da fabricação da maduramicina Maduramicina de amonio, en solución alcohólica, de la fabricación de maduramicina Maduramicin ammonium in alcoholic solution, from the manufacture of maduramicin 38249919 10 382499 3990 3639 3 59899 240 2000 2029 1499 Outros produtos intermediários da fabricação de antibióticos ou de vitaminas ou de outros produtos da posição 29.36 Otros productos intermedios de la fabricación de antibióticos o vitaminas u otros productos de la Partida 29.36, Other intermediate products for the manufacture of antibiotics or of vitamins or other products of Heading 29.36 38249921 10 382499 3990 3639 3 59899 240 2000 2029 1499 Ácidos graxos dimerizados; preparações contendo ácidos graxos dimerizados Ácidos grasos dimerizados; preparaciones que contienen ácidos grasos dimerizados Dimerized fatty acids; preparations containing dimerized fatty acids 38249922 10 382499 3990 3639 3 59899 240 2000 2029 1499 Preparações contendo estearoilbenzoilmetano e palmitoilbenzoilmetano; preparações contendo caprilato e caprato de propilenoglicol Las preparaciones que contienen estearoilbenzoilmetano y palmitoilbenzoilmetano; preparations que contienen caprilato y caprato de propilenoglicol Preparations containing stearoyl benzoyl methane and palmitoyl benzoylmethane; preparations containing caprylate and caprate of propylene glycol 38249923 10 382499 3990 3639 3 59899 240 2000 2029 1499 Preparações contendo triglicerídios dos ácidos caprílico e cáprico Las preparaciones que contienen triglicéridos de los ácidos caprílico y cáprico Preparations containing triglycerides of caprylic and capric acids 38249924 10 382499 3990 3639 3 59899 240 2000 2029 1499 Ésteres de álcoois graxos de C12 a C20 do ácido metacrílico e suas misturas; ésteres de ácidos monocarboxílicos de C10 ramificados com glicerol Ésteres de alcoholes grasos de C12 a C20 del ácido metacrílico y mezclas de los mism

In [0]:
mapping_columns = {
    'CO_NCM':'cod_ncm',
    'CO_UNID':'cod_unidade',
    'CO_SH6':'cod_sh6',
    'CO_PPE':'cod_ppe',
    'CO_PPI':'cod_ppi',
    'CO_FAT_AGREG':'cod_fat_agreg',
    'CO_CUCI_ITEM':'cod_cuci_item',
    'CO_CGCE_N3':'co_cgce_n3',
    'CO_SIIT':'cod_siit',
    'CO_ISIC_CLASSE':'cod_isic_classe',
    'CO_EXP_SUBSET':'cod_exportacao_subset',
    'NO_NCM_POR':'nm_portugues'
}

In [0]:
from pyspark.sql.functions import col

# Crie um DataFrame a partir da consulta SQL
df = spark.sql("""
SELECT DISTINCT *
FROM bronze.co_ncm

""")


# Renomeie as colunas de acordo com o mapeamento
for old_col, new_col in mapping_columns.items():
    df = df.withColumnRenamed(old_col, new_col)

In [0]:
lista_columns = ['NO_NCM_ESP', 'NO_NCM_ING']

In [0]:
df = df.drop(*lista_columns)

In [0]:
# Crie a view temporária com o DataFrame renomeado
df.createOrReplaceTempView('vw_co_ncm')

In [0]:
permanent_table = "d_ncm"

df.write.format("parquet").saveAsTable(permanent_table)

In [0]:
%sql

-- mudando a tabela para o schema silver

CREATE TABLE IF NOT EXISTS gold.d_nomenclatura_mercosul AS SELECT * FROM default.d_ncm;

num_affected_rows num_inserted_rows

In [0]:
%sql
drop table default.d_ncm

In [0]:
%sql
select count(1), nm_portugues as contagem
from gold.d_nomenclatura_mercosul
group by nm_portugues

count(1) contagem 2 Imunoglobulina e cloridrato de histamina, associados 2 2-Cloro-1,3-dinitrobenzeno 1 Sépias e lulas, em outras formas 1 Feijões (Vigna spp., Phaseolus spp.), não cozidos ou cozidos em água ou vapor, congelados. 1 Outros sucos de uvas 1 Outras matérias pécticas, pectinatos e pectatos 1 Ácido 2-hidroxi-4-(metiltio)butanóico e seu sal cálcico 1 Ketamina e seus outros sais 1 Medicamento contendo cefalosporinas/cefamicinas/etc, exceto em doses 1 Ascorbato de sódio, não misturado 2 Menotropinas 1 Sulfatos de cromo 1 Óxidos de germanio 1 Urânio natural e seus compostos; ligas, dispersões (incluindo os ceramais (cermets)), produtos cerâmicos e misturas que contenham urânio natural ou compostos de urânio natural 1 Cinzas e resíduos contendo titânio 1 Minérios de tungstênio (volfrâmio) e seus concentrados 1 Reservatórios, cisternas, cubas e recipientes análogos, de capacidade superior a 300 litros, de plástico 1 Goma xantana, em formas primárias 1 Absorventes e outros artigos higiênicos, de papel 1 Madeira de freixo (Fraxinus spp.), serrada ou fendida longitudinalmente, cortada transversalmente ou desenrolada, mesmo aplainada, lixada ou unida pelas extremidades, de espessura superior a 6 mm 1 Sais duplos e misturas de nitrato de cálcio e nitrato de amônio 1 Outros filmes, sensibilizados, não impressionados, em rolos, de largura superior a 610 mm e comprimento não superior a 200 m 1 Lignossulfonatos 1 Tubo refratrário, de carboneto de silício 1 Camisolões e pijamas, de malha, de uso masculino, de algodão 1 Ferro-níquel 2 Ladrilhos, cubos, pastilhas e artigos semelhantes, mesmo de forma diferente da quadrada ou retangular, cuja maior superfície possa ser inscrita num quadrado de lado inferior a 7 cm 1 Sobretudos, japonas, gabões, capas, anoraques, casacos e semelhantes, de malha, de uso masculino, exceto os artefatos da posição 61.03, de outras matérias têxteis 1 Outros tecidos de malha, de fibras sintéticas, tingidos 1 Tecidos de algodão que contenham pelo menos 85 %, em peso, de algodão, crus, em ponto de tafetá, com peso não superior a 100 g/m2 1 Outros objetos de vidro, para toucador, escritório, etc. 1 Outros fios de alta tenacidade, de poliésteres, náilon ou de outras poliamidas, ou de raiom viscose, impregnados ou revestidos 1 Tecidos que contenham pelo menos 85 %, em peso, de fibras artificiais descontínuas, tintos 1 Fios simples de algodão,de fibras penteadas,que contenham pelo menos 85 %, em peso, de algodão,não acondicionados para venda a retalho, de título inferior a 125 decitex mas não inferior a 106,38 decitex (número métrico superior a 80 mas não superior a 94) 1 Leitores de caracteres magnetizaveis 1 Máquinas e aparelhos para fabricação de pincéis, brochas ou escovas 1 Folha de cobre refinado sem suporte, espessura <= 0.7 mm, pureza >= 99,85% 1 Máquinas e aparelhos de impressão por meio de blocos, cilindros e outros elementos de impressão, para serigrafia 1 Outras bobinas de reatância e de auto-indução 1 Lousas e quadros para escrever ou desenhar, mesmo emoldurados 1 Caixas de relógios, de metais preciosos ou de metais folheados ou chapeados de metais preciosos (plaquê) 1 Selecionadores de frutas 1 Monitores de vídeo, policromáticos, com dispositivos de seleção de varredura (underscanning) e de retardo de sincronismo horizontal e vertical (H/V delay ou pulse cross) 1 Outros aparelhos receptores radiodifusores, combinados com toca-fitas, à pilha ou eletricidade 1 Perfluoroctanossulfonato de amônio 1 Madeira em bruto, mesmo descascada, desalburnada ou esquadriada, tratada com tinta, creosoto ou outros agentes de conservação, de coníferas 1 Perfluoroctanossulfonato de dietanolamônio 1 Garoupas (acanthistius spp.), fresco ou refrigerado 2 Tiocolquicósido 1 Tilápias, bagre, carpas, enguia, salgado, não seco, não defumado 1 Curimatas, peixes congelados, exceto filés, outras carnes, etc 1 Bochechas (cheeks) de merluza antártica (Dissostichus mawsoni), frescos, refrigerados ou congelados 1 Aspargos frescos ou re

In [0]:
new_df = spark.sql("""
SELECT distinct *
FROM bronze.co_ncm

""")
new_df.createOrReplaceTempView('vw_ncm_distinct')

In [0]:
%sql
select count(1)
from vw_ncm_distinct

count(1) 13123

In [0]:
%sql
select count(1)
from gold.d_nomenclatura_mercosul

count(1) 13127